In [1]:
# Import necessary libraries

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns


from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from lightgbm import LGBMClassifier
from sklearn.ensemble import RandomForestClassifier,GradientBoostingClassifier
from sklearn.ensemble import AdaBoostClassifier,StackingClassifier
from catboost import CatBoostClassifier
from xgboost import XGBClassifier

from sklearn.metrics import accuracy_score,precision_score,recall_score,confusion_matrix,f1_score

import time

import warnings
warnings.filterwarnings("ignore")

In [2]:
# load the data

heart_df  = pd.read_csv("heart.csv")

In [3]:
# let's look at the first few entries

heart_df.head()

age  sex  cp  trtbps  chol  fbs  restecg  thalachh  exng  oldpeak  slp  \
0   63    1   3     145   233    1        0       150     0      2.3    0   
1   37    1   2     130   250    0        1       187     0      3.5    0   
2   41    0   1     130   204    0        0       172     0      1.4    2   
3   56    1   1     120   236    0        1       178     0      0.8    2   
4   57    0   0     120   354    0        1       163     1      0.6    2   

   caa  thall  output  
0    0      1       1  
1    0      2       1  
2    0      2       1  
3    0      2       1  
4    0      2       1

In [4]:
print("The shape of the dataset is : {}".format(heart_df.shape))

The shape of the dataset is : (303, 14)


- Age : Age of the patient

- Sex : Sex of the patient

- exang: exercise induced angina (1 = yes; 0 = no)

- ca: number of major vessels (0-3)

- cp : Chest Pain type chest pain type

   - Value 1: typical angina
   
   - Value 2: atypical angina
   
   - Value 3: non-anginal pain
   
   - Value 4: asymptomatic

- trtbps : resting blood pressure (in mm Hg)

- chol : cholestoral in mg/dl fetched via BMI sensor

- fbs : (fasting blood sugar > 120 mg/dl) (1 = true; 0 = false)

- rest_ecg : resting electrocardiographic results

    - Value 0: normal
    - Value 1: having ST-T wave abnormality (T wave inversions and/or ST elevation or depression of > 0.05 mV)
    - Value 2: showing probable or definite left ventricular hypertrophy by Estes' criteria
    
- thalach : maximum heart rate achieved

- target : 0= less chance of heart attack 1= more chance of heart attack

In [5]:
heart_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 303 entries, 0 to 302
Data columns (total 14 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   age       303 non-null    int64  
 1   sex       303 non-null    int64  
 2   cp        303 non-null    int64  
 3   trtbps    303 non-null    int64  
 4   chol      303 non-null    int64  
 5   fbs       303 non-null    int64  
 6   restecg   303 non-null    int64  
 7   thalachh  303 non-null    int64  
 8   exng      303 non-null    int64  
 9   oldpeak   303 non-null    float64
 10  slp       303 non-null    int64  
 11  caa       303 non-null    int64  
 12  thall     303 non-null    int64  
 13  output    303 non-null    int64  
dtypes: float64(1), int64(13)
memory usage: 33.3 KB


In [6]:
# unique values in each feature
heart_df.nunique()

age          41
sex           2
cp            4
trtbps       49
chol        152
fbs           2
restecg       3
thalachh     91
exng          2
oldpeak      40
slp           3
caa           5
thall         4
output        2
dtype: int64

In [4]:
# check if there is any duplicate
heart_df[heart_df.duplicated()]

age  sex  cp  trtbps  chol  fbs  restecg  thalachh  exng  oldpeak  slp  \
164   38    1   2     138   175    0        1       173     0      0.0    2   

     caa  thall  output  
164    4      2       1

In [5]:
# drop the duplicate row
heart_df.drop_duplicates(inplace=True)

In [6]:
# columns with discrete numeric values
num_cat_cols = ['sex', 'cp', 'fbs', 'restecg', 'exng', 'slp', 'caa', 'thall']
                
for col in num_cat_cols:
    print("column : {}".format(col))            
    print(heart_df[col].value_counts(normalize=True))
    print("\n")            

column : sex
1    0.682119
0    0.317881
Name: sex, dtype: float64


column : cp
0    0.473510
2    0.284768
1    0.165563
3    0.076159
Name: cp, dtype: float64


column : fbs
0    0.850993
1    0.149007
Name: fbs, dtype: float64


column : restecg
1    0.500000
0    0.486755
2    0.013245
Name: restecg, dtype: float64


column : exng
0    0.672185
1    0.327815
Name: exng, dtype: float64


column : slp
2    0.466887
1    0.463576
0    0.069536
Name: slp, dtype: float64


column : caa
0    0.579470
1    0.215232
2    0.125828
3    0.066225
4    0.013245
Name: caa, dtype: float64


column : thall
2    0.546358
3    0.387417
1    0.059603
0    0.006623
Name: thall, dtype: float64




In [9]:
#fig, ax = plt.subplots(2,2,figsize=(14,10))
#sns.distplot(heart_df['trtbps'],ax=ax[0,0])
#sns.distplot(heart_df['chol'],ax=ax[0,1])
#sns.distplot(heart_df['thalachh'],ax=ax[1,0])
#sns.distplot(heart_df['oldpeak'],ax=ax[1,1]);

In [28]:
heart_df.query("chol > 400")

age  sex  cp  trtbps  chol  fbs  restecg  thalachh  exng  oldpeak  slp  \
28    65    0   2     140   417    1        0       157     0      0.8    2   
85    67    0   2     115   564    0        0       160     0      1.6    1   
220   63    0   0     150   407    0        0       154     0      4.0    1   
246   56    0   0     134   409    0        0       150     1      1.9    1   

     caa  thall  output  
28     1      2       1  
85     0      3       1  
220    3      3       0  
246    2      3       0

In [30]:
heart_df.query("oldpeak > 4.0")

age  sex  cp  trtbps  chol  fbs  restecg  thalachh  exng  oldpeak  slp  \
101   59    1   3     178   270    0        0       145     0      4.2    0   
204   62    0   0     160   164    0        0       145     0      6.2    0   
221   55    1   0     140   217    0        1       111     1      5.6    0   
250   51    1   0     140   298    0        1       122     1      4.2    1   
291   58    1   0     114   318    0        2       140     0      4.4    0   

     caa  thall  output  
101    0      3       1  
204    3      3       0  
221    0      3       0  
250    3      3       0  
291    3      1       0

In [7]:
#heart_df['age'].unique()

In [8]:
# feature matrix
X = heart_df.drop("output",axis=1)

# target vector
y = heart_df['output']

In [11]:
y.value_counts(normalize=True)

1    0.544554
0    0.455446
Name: output, dtype: float64

In [9]:
# splitting the dataset into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X,y,test_size=0.2,stratify=y)

In [13]:
print("The shape of the training set : {}".format(X_train.shape))
print("The shape of the test set : {}".format(X_test.shape))

The shape of the training set : (242, 13)
The shape of the test set : (61, 13)


In [10]:
# distribution of classes in train and test target vectors
print("The training set :")
print(y_train.value_counts(normalize=True))
print("\n The test set :")
print(y_test.value_counts(normalize=True))

The training set :
1    0.543568
0    0.456432
Name: output, dtype: float64

 The test set :
1    0.540984
0    0.459016
Name: output, dtype: float64


In [16]:
def build_pipeline(model):
    
    """
    A function to build pipeline with the following steps:
           
           1. 'scaler' : Standardize features by removing the mean and scaling to unit variance.
           2. 'clf' : fit a classifier to the dataset.
           
    Parameter:
    ------------
    model : a classifier object
    
    Returns:
    ----------
    pipeline : a pipeline object
    
    """
    
    pipeline = Pipeline([
                       ('scaler', StandardScaler()),
                       ('clf', model) 
                       ])
    
    return pipeline

In [17]:
def scan_model(pipeline,param_dict,X_train,y_train):
    
    """
    A function to find the optimal set of parameters for a classifier using GridSearchCV.
    
    Parameters:
    ------------
    pipeline : a pipeline object
    
    param_dict : dict
          a dictionary with the names of hyperparameters as keys and the corresponding list of values to be scanned as values
          
    X_train : pandas dataframe
          the feature matrix
          
    y_train : pandas series
          the target vector
    
    Returns:
    ----------
    grid_cv : a GridSearchCV object fitted on the training data
    
    """
    
    grid_cv = GridSearchCV(pipeline,param_grid=param_dict,scoring='accuracy',cv=5,verbose=2)
    grid_cv.fit(X_train,y_train)

    return grid_cv

In [18]:
def eval_model(model,X_test,y_test):
    
    """
    A function to evaluate the performance of a classifier on unseen data.
           
    Parameter:
    ------------
    model : the classifier fitted on the training data
    
    X_test : pandas dataframe
         the feature matrix
         
    y_test : pandas series
         the target vector
    
    Returns:
    ----------
    acc_test : float
         the accuracy score on the test set
         
    f1_test : float
         the f1 score on the test set
         
    tn,fp,fn,tp : integer
         true negative,false positive,false negative and true positive respectively (for the test set)
    
    """
    
    pred_test = model.predict(X_test)
    tn, fp, fn, tp = confusion_matrix(y_test,pred_test).ravel()
    acc_test = accuracy_score(y_test,pred_test)
    prec_test = precision_score(y_test,pred_test)
    recall_test = recall_score(y_test,pred_test)
    f1_test = f1_score(y_test,pred_test)
    
    return acc_test,f1_test,tn,fp,fn,tp

In [22]:
model_list = [LogisticRegression(), DecisionTreeClassifier(), RandomForestClassifier(), KNeighborsClassifier(),
        LGBMClassifier(), GradientBoostingClassifier(), AdaBoostClassifier(), CatBoostClassifier(),
        XGBClassifier()]

lr_dict = {
           'clf__C' : np.arange(0.1,6,0.5),
           'clf__solver': ['liblinear','lbfgs']}

dt_dict = {
           'clf__criterion' : ['gini', 'entropy'],
           'clf__max_features' : ['sqrt','log2'],
           'clf__max_depth' : np.arange(10,60,10)}

rf_dict = {
           'clf__n_estimators': np.arange(20,100,20),
           'clf__criterion' : ['gini', 'entropy'],
           'clf__max_features' : ['sqrt','log2'],
           'clf__max_depth' : np.arange(10,60,10)}

knn_dict = {
            'clf__n_neighbors': np.arange(5,30,5),
            'clf__weights' : ['uniform','distance'],
            'clf__algorithm' : ['auto','ball_tree','kd_tree','brute'],
            'clf__metric' : ['minkowski','euclidean']}

lgbm_dict = {
             'clf__boosting_type': ['gbdt','dart','goss','rf'],
             'clf__n_estimators': np.arange(50,100,10),
             'clf__learning_rate': np.arange(0.1,5,0.5),
             'clf__max_depth': np.arange(2,10,1)}

gb_dict = {
           'clf__loss' : ['deviance','exponential'],
           'clf__learning_rate': np.arange(0.1,5,0.5),
           'clf__n_estimators': np.arange(20,100,20),
           'clf__criterion' : ['friedman_mse','mse','mae'],
           'clf__max_features' : ['sqrt','log2']}

ada_dict = {
           'clf__learning_rate': np.arange(0.1,5,0.5),
           'clf__n_estimators': np.arange(20,100,20),
           'clf__algorithm' : ['SAMME','SAMME.R']}

catb_dict = {
           'clf__learning_rate': np.arange(0.1,5,0.5),
           'clf__n_estimators': np.arange(50,100,10),    
           'clf__auto_class_weights': [None,'balanced','SqrtBalanced']}

xgb_dict = {
           'clf__learning_rate': np.arange(0.1,5,0.5),
           'clf__n_estimators': np.arange(20,100,20),
           'clf__booster':['gbtree','gblinear','dart'],
           'clf__gamma': np.arange(0.1,5,0.5)}

param_list = [lr_dict, dt_dict, rf_dict, knn_dict, lgbm_dict, gb_dict, ada_dict, catb_dict, xgb_dict]

In [23]:
# list to hold the information about classifiers after grid search
scan_list = []

# list to hold the values of TN,FP,FN and TP for each classifier
pred_list = []

for model, param_dict in zip(model_list,param_list):
    print("building model : {}\n".format(str(model).split("(")[0]))
    
     # build the model
    pipeline = build_pipeline(model)
    start_time = time.time()      
    
    # perform grid search and fit the best model to the training set
    grid_cv = scan_model(pipeline,param_dict,X_train,y_train)
    print("\n model fitted!")
    elapsed_time = time.time() - start_time  
    
     # evaluate the model
    acc_test,f1_test,tn,fp,fn,tp = eval_model(grid_cv,X_test,y_test)   
      
    scan_list.append({
              'model': str(model).split("(")[0],
              'best_score': grid_cv.best_score_,
              'test_acc': acc_test,
              'test_f1': f1_test,
              'best_params':grid_cv.best_params_,
              'time':elapsed_time
    })      
          
          
    pred_list.append({
              'model': str(model).split("(")[0],
              'true_neg':tn,
              'false_pos':fp,
              'false_neg':fn,
              'true_pos':tp
    })      

building model : LogisticRegression

Fitting 5 folds for each of 24 candidates, totalling 120 fits
[CV] END ..................clf__C=0.1, clf__solver=liblinear; total time=   0.0s
[CV] END ..................clf__C=0.1, clf__solver=liblinear; total time=   0.0s
[CV] END ..................clf__C=0.1, clf__solver=liblinear; total time=   0.0s
[CV] END ..................clf__C=0.1, clf__solver=liblinear; total time=   0.0s
[CV] END ..................clf__C=0.1, clf__solver=liblinear; total time=   0.0s
[CV] END ......................clf__C=0.1, clf__solver=lbfgs; total time=   0.0s
[CV] END ......................clf__C=0.1, clf__solver=lbfgs; total time=   0.0s
[CV] END ......................clf__C=0.1, clf__solver=lbfgs; total time=   0.0s
[CV] END ......................clf__C=0.1, clf__solver=lbfgs; total time=   0.0s
[CV] END ......................clf__C=0.1, clf__solver=lbfgs; total time=   0.0s
[CV] END ..................clf__C=0.6, clf__solver=liblinear; total time=   0.0s
[CV] END .

[CV] END clf__criterion=gini, clf__max_depth=10, clf__max_features=sqrt; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=10, clf__max_features=sqrt; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=10, clf__max_features=sqrt; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=10, clf__max_features=log2; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=10, clf__max_features=log2; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=10, clf__max_features=log2; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=10, clf__max_features=log2; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=10, clf__max_features=log2; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=sqrt; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=sqrt; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=sqrt; total t

[CV] END clf__criterion=entropy, clf__max_depth=50, clf__max_features=sqrt; total time=   0.0s
[CV] END clf__criterion=entropy, clf__max_depth=50, clf__max_features=sqrt; total time=   0.0s
[CV] END clf__criterion=entropy, clf__max_depth=50, clf__max_features=sqrt; total time=   0.0s
[CV] END clf__criterion=entropy, clf__max_depth=50, clf__max_features=log2; total time=   0.0s
[CV] END clf__criterion=entropy, clf__max_depth=50, clf__max_features=log2; total time=   0.0s
[CV] END clf__criterion=entropy, clf__max_depth=50, clf__max_features=log2; total time=   0.0s
[CV] END clf__criterion=entropy, clf__max_depth=50, clf__max_features=log2; total time=   0.0s
[CV] END clf__criterion=entropy, clf__max_depth=50, clf__max_features=log2; total time=   0.0s

 model fitted!
building model : RandomForestClassifier

Fitting 5 folds for each of 80 candidates, totalling 400 fits
[CV] END clf__criterion=gini, clf__max_depth=10, clf__max_features=sqrt, clf__n_estimators=20; total time=   0.0s
[CV] EN

[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=log2, clf__n_estimators=40; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=log2, clf__n_estimators=40; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=log2, clf__n_estimators=40; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=log2, clf__n_estimators=40; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=log2, clf__n_estimators=60; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=log2, clf__n_estimators=60; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=log2, clf__n_estimators=60; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=log2, clf__n_estimators=60; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=20, clf__max_features=log2, clf__n_estimato

[CV] END clf__criterion=gini, clf__max_depth=40, clf__max_features=sqrt, clf__n_estimators=80; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=40, clf__max_features=log2, clf__n_estimators=20; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=40, clf__max_features=log2, clf__n_estimators=20; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=40, clf__max_features=log2, clf__n_estimators=20; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=40, clf__max_features=log2, clf__n_estimators=20; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=40, clf__max_features=log2, clf__n_estimators=20; total time=   0.0s
[CV] END clf__criterion=gini, clf__max_depth=40, clf__max_features=log2, clf__n_estimators=40; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=40, clf__max_features=log2, clf__n_estimators=40; total time=   0.1s
[CV] END clf__criterion=gini, clf__max_depth=40, clf__max_features=log2, clf__n_estimato

...

[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=2.1, clf__n_estimators=80; total time=   0.0s
[20:25:38] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=2.1, clf__n_estimators=80; total time=   0.0s
[20:25:38] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=2.6, clf__n_estimators=20; total time=   0.0s
[20:25:38] WARNING: /home/conda/fee

[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=3.1, clf__n_estimators=60; total time=   0.0s
[20:25:39] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=3.1, clf__n_estimators=60; total time=   0.0s
[20:25:39] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=3.1, clf__n_estimators=60; total time=   0.0s
[20:25:39] WARNING: /home/conda/fee

[20:25:39] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=3.6, clf__n_estimators=60; total time=   0.0s
[20:25:39] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=3.6, clf__n_estimators=80; total time=   0.0s
[20:25:39] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the de

[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=4.1, clf__n_estimators=80; total time=   0.0s
[20:25:39] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=4.1, clf__n_estimators=80; total time=   0.0s
[20:25:39] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[CV] END clf__booster=dart, clf__gamma=4.6, clf__learning_rate=4.1, clf__n_estimators=80; total time=   0.0s
[20:25:39] WARNING: /home/conda/fee

[20:25:40] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:541: 
Parameters: { gamma } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[20:25:40] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost_1607604574104/work/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.

 model fitted!


In [24]:
scan_df = pd.DataFrame(scan_list)
pred_df = pd.DataFrame(pred_list)

In [25]:
scan_df

model  best_score  test_acc  \
0                                 LogisticRegression    0.830527  0.852459   
1                             DecisionTreeClassifier    0.793622  0.737705   
2                             RandomForestClassifier    0.838861  0.836066   
3                               KNeighborsClassifier    0.822194  0.786885   
4                                     LGBMClassifier    0.834949  0.868852   
5                         GradientBoostingClassifier    0.830867  0.868852   
6                                 AdaBoostClassifier    0.818452  0.819672   
7  <catboost.core.CatBoostClassifier object at 0x...    0.839031  0.836066   
8                                      XGBClassifier    0.826276  0.803279   

    test_f1                                        best_params        time  
0  0.873239            {'clf__C': 0.1, 'clf__solver': 'lbfgs'}    1.012796  
1  0.750000  {'clf__criterion': 'entropy', 'clf__max_depth'...    0.708729  
2  0.852941  {'clf__criterion': 'entropy', 'clf__max_depth'...   26.534620  
3  0.821918  {'clf__algorithm': 'auto', 'clf__metric': 'min...    3.153226  
4  0.885714  {'clf__boosting_type': 'goss', 'clf__learning_...  106.014779  
5  0.882353  {'clf__criterion': 'mse', 'clf__learning_rate'...   94.675968  
6  0.835821  {'clf__algorithm': 'SAMME', 'clf__learning_rat...   21.302036  
7  0.857143  {'clf__auto_class_weights': 'SqrtBalanced', 'c...   79.709272  
8  0.823529  {'clf__booster': 'gblinear', 'clf__gamma': 0.1...  113.117007

In [26]:
pred_df

model  true_neg  false_pos  \
0                                 LogisticRegression        21          7   
1                             DecisionTreeClassifier        21          7   
2                             RandomForestClassifier        22          6   
3                               KNeighborsClassifier        18         10   
4                                     LGBMClassifier        22          6   
5                         GradientBoostingClassifier        23          5   
6                                 AdaBoostClassifier        22          6   
7  <catboost.core.CatBoostClassifier object at 0x...        21          7   
8                                      XGBClassifier        21          7   

   false_neg  true_pos  
0          2        31  
1          9        24  
2          4        29  
3          3        30  
4          2        31  
5          3        30  
6          5        28  
7          3        30  
8          5        28

In [43]:
scan_df.iloc[5][4]

{'clf__criterion': 'mse',
 'clf__learning_rate': 0.1,
 'clf__loss': 'exponential',
 'clf__max_features': 'log2',
 'clf__n_estimators': 20}

In [46]:
scan_df.iloc[5][4]

{'clf__algorithm': 'SAMME', 'clf__learning_rate': 0.6, 'clf__n_estimators': 80}

Best model so far is LGBMClassifier. Let's further tune it's hyperparameters.

In [36]:
model = LGBMClassifier(boosting_type='goss',learning_rate=0.1,max_depth=5)
pipeline = build_pipeline(model)
param_dict = {'clf__n_estimators':np.arange(80,200,20)}
grid_cv = GridSearchCV(pipeline,param_dict,cv=10,verbose=2)

fitted_model = grid_cv.fit(X_train,y_train)

Fitting 10 folds for each of 6 candidates, totalling 60 fits
[CV] END ...............................clf__n_estimators=80; total time=   0.1s
[CV] END ...............................clf__n_estimators=80; total time=   0.0s
[CV] END ...............................clf__n_estimators=80; total time=   0.0s
[CV] END ...............................clf__n_estimators=80; total time=   0.0s
[CV] END ...............................clf__n_estimators=80; total time=   0.0s
[CV] END ...............................clf__n_estimators=80; total time=   0.0s
[CV] END ...............................clf__n_estimators=80; total time=   0.0s
[CV] END ...............................clf__n_estimators=80; total time=   0.1s
[CV] END ...............................clf__n_estimators=80; total time=   0.0s
[CV] END ...............................clf__n_estimators=80; total time=   0.0s
[CV] END ..............................clf__n_estimators=100; total time=   0.0s
[CV] END ..............................clf__n_es

In [37]:
fitted_model.best_params_

{'clf__n_estimators': 140}

In [38]:
fitted_model.best_score_

0.8473333333333333

In [39]:
accuracy_score(y_train,fitted_model.predict(X_train))

0.9173553719008265

In [41]:
# predict on the test set

preds = fitted_model.predict(X_test)
acc_score = accuracy_score(y_test,preds)

print("The final accuracy score for the test set : {}".format(acc_score))

The final accuracy score for the test set : 0.8688524590163934


In [31]:
#scan_df.iloc[0]

In [32]:
#scan_df.iloc[3]

In [33]:
#scan_df.iloc[5][4]

In [46]:
lr_pipeline = build_pipeline(LogisticRegression(C=0.1,solver='lbfgs'))
gbb_pipeline = build_pipeline(GradientBoostingClassifier(criterion='mse',learning_rate=0.1,loss='exponential',
                                                         max_features='log2',n_estimators=20))
lgbm_pipeline = build_pipeline(LGBMClassifier(boosting_type='goss',learning_rate=0.1,max_depth=5,n_estimators=140))

est_list = [('LGBM',lgbm_pipeline), ('LR',lr_pipeline), ('GBB',gbb_pipeline)] 
stacked_clf = StackingClassifier(estimators=est_list,cv=5,passthrough=False)

stacked_clf.fit(X_train,y_train)

preds = stacked_clf.predict(X_test)
score_acc = accuracy_score(y_test,preds)
#f1_score(y_test,preds)

In [47]:
score_acc

0.8688524590163934

In [78]:
preds

array([0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0,
       1, 1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 0,
       1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 0])

In [79]:
y_test.values

array([0, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0,
       1, 1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 1, 1, 0,
       0, 0, 0, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 1, 0])

In [49]:
confusion_matrix(y_test,preds)

array([[22,  6],
       [ 2, 31]])